<a href="https://colab.research.google.com/github/youseungH/changyi/blob/main/Crawling_oneyear.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

필요한 패키지

In [ ]:
from bs4 import BeautifulSoup
import requests
import pandas as pd

데이터 불러오기

In [ ]:
url="https://www.safetydata.go.kr/disaster-data/disasterNotification?searchStartDttm=&searchEndDttm=&keyword=&orderBy=&currentPage=1&cntPerPage=12000&pageSize=12000"

response=requests.get(url)

if response.status_code == 200:
    file_path = "disaster_message.html"

    with open(file_path, "w", encoding="utf-8") as file:
        file.write(response.text)

    print(f"HTML content has been downloaded and saved to {file_path}.")
else:
    print(f"Failed to retrieve the page. Status code: {response.status_code}")

filename="disaster_message.html"
html=""
with open (filename, 'r', encoding='UTF-8') as file:
    for line in file:
        html+=line

HTML content has been downloaded and saved to disaster_message.html.


html parsing 및 구조 파악

In [ ]:
soup=BeautifulSoup(html,'lxml')
print(soup)

<!DOCTYPE html>
<html lang="ko">
<head>
<meta charset="utf-8"/>
<meta content="IE=edge" http-equiv="X-UA-Compatible"/>
<meta content="width=device-width, initial-scale=1.0" name="viewport"/>
<link href="/img/favicon.ico" rel="shortcut icon" type="image/x-icon"/>
<script src="/js/jquery-1.11.1.min.js"></script>
<title>재난 문자 | 재난안전데이터공유플랫폼</title>
<meta content="재난안전데이터 공유 플랫폼에서는 원하는 데이터를 찾을 수 있도록 기능을 제공합니다. 찾고 싶은 데이터명을 입력하여 데이터명과 일치하는 재난안전데이터를 찾을 수 있습니다." name="description"/>
<meta content="재난안전데이터, 공공데이터, 재난, 풍수해, 오픈데이터, 안전데이터" name="keywords"/>
<meta content="website" property="og:type"/>
<meta content="https://www.safetydata.go.kr/" property="og:url"/>
<meta content="재난안전데이터공유플랫폼" property="og:title"/>
<meta content="재난안전데이터 공유 플랫폼에서는 원하는 데이터를 찾을 수 있도록 기능을 제공합니다. 찾고 싶은 데이터명을 입력하여 데이터명과 일치하는 재난안전데이터를 찾을 수 있습니다." property="og:description"/>
<meta content="재난안전데이터공유플랫폼" property="og:site_name"/>
<meta content="ko_KR" property="og:locale"/>
<link href="/css/style.css" rel="stylesheet"/>


Df 만들기

In [ ]:
rows=soup.find_all('tr')

for row in rows:
    cols=row.find_all('td')
    cols=[ele.text.strip() for ele in cols]
    data_list.append(cols)

df=pd.DataFrame(data_list, columns=['number','text','time'])

pd.set_option('display.max_colwidth', None)
pd.set_option('display.width', None)
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)

df=df.drop(0)
df=df.reset_index(drop=True)
print(df.head())
print(df.tail())

  number  \
0  11666   
1  11665   
2  11664   
3  11663   
4  11662   

                                                                                          text  \
0   현재 폭염경보 발효 중\n△낮 시간 야외활동 삼가기\n△카페인음료 및 주류 삼가기\n△자택에 냉방기 없는 경우 무더위쉼터로 이동하여 건강에 유의바랍니다[의성군]N   
1              금일 17시~18시 양수발전소 하부댐 초당 47.5톤방류 예정, 하천수위 상승이 예상되오니, 하천 주변 접근을 자제하시기 바랍니다.[무주군]N   
2        폭염경보 발효중이오니, 장시간 야외활동과 한낮 야외작업(논,밭,건설현장 등)을 자제하시고 그늘에서 휴식을 취하는 등 건강관리에 유의바랍니다. [상주시]N   
3  현재 폭염특보 발효중. 농사일, 건설현장작업, 야외활동 시 충분한 물 섭취와 그늘 휴식, 주변 노약자분들께 안부 확인등 안전관리에 유의하시기 바랍니다.[충청북도]N   
4   춘천시 주민인 고정희씨(여,87세)를 찾습니다- 160cm,흰머리,벌집무늬반팔티,검정신발,버버리문양보행보조기 사용 vo.la/SNyTC /☎182 [강원경찰청]N   

                  time  
0  2024/07/26 15:04:12  
1  2024/07/26 14:58:33  
2  2024/07/26 14:58:03  
3  2024/07/26 14:56:43  
4  2024/07/26 14:49:49  
       number  \
163332      5   
163333      4   
163334      3   
163335      2   
163336      1   

                                                                                     

결측치, 중복치 제거 후 number column을 index로 만듦.

In [ ]:
df=df.dropna()
df = df.drop_duplicates()
df['number']=pd.to_numeric(df['number'])
df = df.sort_values(by='number', ascending=True)
df = df.set_index('number')
print(df.head())
print(df.tail())

                                                                                               text  \
number                                                                                                
1           [중구청]오늘 00시30분 부산지역 호우경보 발효. 많은 비와 낙뢰가 예상되오니 저지대, 침수위험지역 접근금지 및 외출자제 등 안전에 유의하시기 바랍니다.N   
2          [전북경찰청] 완주군에서 배회중인 민도식씨(남,70세)를 찾습니다-160cm,회색줄무늬티,검정칠부등산바지,검정운동화,지팡이 vo.la/TXWtJ / ☎182N   
3       [전북경찰청]전주시에서 실종된 민도식씨(남,70세)를 찾습니다-160cm,55kg,회색줄무늬티,검정칠부등산바지,검정운동화,지팡이\nvo.la/TXWtJ/ ☎182N   
4       [의령군]현재 지방도 1040호선 의령읍 정암리~만천리 구간(정암철교~수협사료 삼거리) 비탈면 토석유출로 전면 통제중이니, 교통정보 확인 후 우회하시기 바랍니다.N   
5           [행정안전부] 많은 비가 내리고 있습니다. 가급적 대중교통을 이용하시고, 운전 시 지하차도 등 저지대는 침수우려가 있으니 속도를 줄이고 안전운전 바랍니다.N   

                       time  
number                       
1       2023/09/01 01:18:57  
2       2023/09/01 08:29:07  
3       2023/09/01 08:22:00  
4       2023/09/01 07:06:46  
5       2023/09/01 06:54:35  
                                                                    

<ipython-input-40-df5a7fc1e309>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['number']=pd.to_numeric(df['number'])


content에서 위치정보 분리해서 따로 만듦

In [ ]:
def extract_location(text):
    if text is None:
        return text, 'NaN'
    start=text.rfind('[')
    end=text.rfind(']')
    if start!=-1 and end!=-1:
        location=text[start+1:end]
        text=text[:start]+text[end+1:]
    else:
        location='NaN'
    return text.strip(), location

df[['text', 'location']] = df['text'].apply(lambda x: pd.Series(extract_location(x)))

pd.set_option('display.max_colwidth', None)

print(df.head())
print(df.tail())

                                                                                          text  \
number                                                                                           
1           오늘 00시30분 부산지역 호우경보 발효. 많은 비와 낙뢰가 예상되오니 저지대, 침수위험지역 접근금지 및 외출자제 등 안전에 유의하시기 바랍니다.N   
2             완주군에서 배회중인 민도식씨(남,70세)를 찾습니다-160cm,회색줄무늬티,검정칠부등산바지,검정운동화,지팡이 vo.la/TXWtJ / ☎182N   
3         전주시에서 실종된 민도식씨(남,70세)를 찾습니다-160cm,55kg,회색줄무늬티,검정칠부등산바지,검정운동화,지팡이\nvo.la/TXWtJ/ ☎182N   
4       현재 지방도 1040호선 의령읍 정암리~만천리 구간(정암철교~수협사료 삼거리) 비탈면 토석유출로 전면 통제중이니, 교통정보 확인 후 우회하시기 바랍니다.N   
5              많은 비가 내리고 있습니다. 가급적 대중교통을 이용하시고, 운전 시 지하차도 등 저지대는 침수우려가 있으니 속도를 줄이고 안전운전 바랍니다.N   

                       time location  
number                                
1       2023/09/01 01:18:57      중구청  
2       2023/09/01 08:29:07    전북경찰청  
3       2023/09/01 08:22:00    전북경찰청  
4       2023/09/01 07:06:46      의령군  
5       2023/09/01 06:54:35    행정안전부  
                                        